[![image](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/lukemlawley/RapidNomad/blob/main/RapidNomad_014122023.ipynb)

In [5]:
import fiona
import geopandas
import folium
import geosdemo

In [6]:
from IPython.display import display, HTML
knoxroads = geopandas.read_file("\\Users\lukmlawl\Rapid-Nomad\RapidNomad\KnoxCountyRoads\KnoxCountyRoads.shp")
#road_search = input("Enter a road name to search for: ")
#search = knoxroads.loc[knoxroads["FULLNAME"] == road_search]
#search.drop('geometry', axis = 1, inplace = True)
#att_table = search.to_html(index = False, classes = 'table table-striped table-hover')
#html = f'<div style="height: 200px; overflow-y: scroll;">{att_table}</div>'
att_table = knoxroads.to_html(index = False, classes='table table-striped table-hover')
html = f'<div style="height: 200px; overflow-y: scroll;">{att_table}</div>'
display(HTML(html))

In [ ]:
class Map(folium.Map):
    def __init__(self, location = [35.9986, -83.9413], zoom_start = 10, **kwargs):
        super().__init__(location = location, zoom_start = zoom_start, **kwargs)
    def add_basemap(self, basemap="HYBRID", show=True, **kwargs):
        import xyzservices
        basemaps = Box(xyz_to_folium(), frozen_box=True)
        try:
            if isinstance(basemap, xyzservices.TileProvider):
                name = basemap.name
                url = basemap.build_url()
                attribution = basemap.attribution
                if "max_zoom" in basemap.keys():
                    max_zoom = basemap["max_zoom"]
                else:
                    max_zoom = 22
                layer = folium.TileLayer(
                    tiles=url,
                    attr=attribution,
                    name=name,
                    max_zoom=max_zoom,
                    overlay=True,
                    control=True,
                    show=show,
                    **kwargs,
                )

                self.add_layer(layer)

                arc_add_layer(url, name)

            elif basemap in basemaps:
                bmap = basemaps[basemap]
                bmap.show = show
                bmap.add_to(self)
                if isinstance(basemaps[basemap], folium.TileLayer):
                    url = basemaps[basemap].tiles
                elif isinstance(basemaps[basemap], folium.WmsTileLayer):
                    url = basemaps[basemap].url
                arc_add_layer(url, basemap)
            else:
                print(
                    "Basemap can only be one of the following: {}".format(
                        ", ".join(basemaps.keys())
                    )
                )

        except Exception:
            raise Exception(
                "Basemap can only be one of the following: {}".format(
                    ", ".join(basemaps.keys())
                )
            )

    #def add_basemap(self, basemaps = 'OpenStreetMap'):
        #for basemap in basemaps:
            #url = f'https://tiles.wmflabs.org/{basemap}/{{z}}/{{x}}/{{y}}.png'
            #tile_layer = folium.TileLayer(tiles=url, name=basemap, attr=' '.join(['Map data', basemap]))
            #tile_layer.add_to(self)
    def add_layer_control(self):
        layer_ctrl = False
        for item in self.to_dict()["children"]:
            if item.startswith("layer_control"):
                layer_ctrl = True
                break
            if not layer_ctrl:
                folium.LayerControl().add_to(self)
from folium.plugins import FeatureGroupSubGroup as fgsg
knoxroads_shp = folium.FeatureGroup(name = 'Knox County Roads')
folium.GeoJson(knoxroads).add_to(knoxroads_shp)
roads_layer = fgsg(knoxroads_shp, 'Knox County Roads')
m = Map()
m.add_basemap(["BlackAndWhite", "OpenSeaMap", "OpenTopoMap", "OSMBright", "Neighbourhood"])
roads_layer.add_to(m)
m

In [4]:
import folium
m = folium.Map(location = [35.9986, -83.9413], zoom_start = 12)
m